In [2]:
import sys
%conda install --yes --prefix {sys.prefix} pymatreader
%conda install --yes --prefix {sys.prefix} pandas

from pymatreader import read_mat
import pandas as pd
import numpy as np
import datetime
import time


Note: you may need to restart the kernel to use updated packages.



EnvironmentLocationNotFound: Not a conda environment: c:\Users\Karlj\dissertation\UsersKarljanaconda3


EnvironmentLocationNotFound: Not a conda environment: c:\Users\Karlj\dissertation\UsersKarljanaconda3




Note: you may need to restart the kernel to use updated packages.


In [4]:
data = read_mat('C:\\Users\\Karlj\\dissertation\\wifimod\\S1_S47\\I1\\S1_S47_I1_T1.mat')

In [5]:
data.keys()

dict_keys(['__header__', '__version__', '__globals__', 'Raw_Cell_Matrix'])

In [32]:
df = pd.DataFrame(data['Raw_Cell_Matrix'])
# print(data['Raw_Cell_Matrix'])
df = df.drop(['Nrx', 'Ntx', 'noise','agc','RSSI_a', 'RSSI_b','RSSI_c', "timestamp_low"], axis=1)


[{'timestamp_low': 1.8446744073241686e+19, 'Nrx': 3, 'Ntx': 2, 'noise': -68, 'agc': 44, 'RSSI_a': 40, 'RSSI_b': 39, 'RSSI_c': 35, 'CSI': array([[[  2.+12.j,  13. -7.j,   8.-11.j, -12.-11.j, -17.+20.j,
           2.+10.j,  16.+11.j,  13. -5.j,   7.-16.j, -15.-14.j,
         -11. -9.j, -24. +3.j,  -1.+21.j,  28.+23.j,  32. +8.j,
          25.-17.j,  -7.-17.j, -22.-11.j, -24. +5.j, -11.+18.j,
           9.+13.j,  23. +1.j,  23.-15.j,   2.-19.j, -17.-10.j,
         -16.+16.j,   2.+24.j,  12. +8.j,   5. -8.j,  -3. -9.j],
        [ 10. +2.j,   5. -7.j, -13.-11.j, -15. +8.j,   2.+11.j,
          15.+22.j,  19. -8.j,   4.-16.j, -15.-16.j, -19. -2.j,
         -29.+11.j,   0.+33.j,  24.+25.j,  36. -8.j,  32.-14.j,
           4.-36.j, -19.-24.j, -36. +7.j, -24.+30.j,   6.+29.j,
          27.+13.j,  32.-14.j,   6.-37.j, -18.-34.j, -41. +7.j,
          -3.+44.j,  35.+14.j,  27.-15.j,  -8.-24.j, -28. -6.j],
        [ 16.-11.j, -17.-12.j, -24. +4.j,  -3.+28.j,  35. +8.j,
          17.-12.j,  -2.-29.j

In [39]:
def standardise(array):
    standardise = lambda x, y, z: (x-y)/z
    csistd = np.frompyfunc(standardise, 3, 1)
    mean = np.mean(array)
    std = np.std(array)
    return csistd(array,mean,std)
    
def preprocess(df, active, steady):
    #Extracting the amplitude
    df['CSI'] = np.abs(df['CSI'])
    
    #Using the equation from CSITime, standardize each sample
    df['Standardised'] = [standardise(sample) for sample in df["CSI"]]
    df.drop("CSI", inplace = True, axis = 1)
    
    
    
preprocess(df, 'I1','I13')
print(df.head())
print(df.shape)
    

  label                                       Standardised
0    I1  [[[-1.1555606530164928, -1.0370904823417137, -...
1    I1  [[[-1.10026568117602, -1.1932842564062538, -0....
2    I1  [[[-1.3005949454504662, -1.0942090307267613, -...
3    I1  [[[-0.8965384569876858, -0.743717113596672, -1...
4    I1  [[[-1.4412201746708004, -1.1468885131184607, -...
(1768, 2)


In [81]:
def segmentation(df):
    #Window size is 256, stride is 128
    segmented = pd.DataFrame({'Range': 'string', 'Sample': []})
    stride = 128
    startIndex = 0
    lastIndex = 256
    while(lastIndex < df.shape[0]):
        sample = df['Standardised']
        sample = sample.iloc[startIndex:lastIndex].to_numpy()
        index = '{}-{}'.format(startIndex, lastIndex)
        newRow = pd.Series({'Range' : index, 'Sample' : sample})
        segmented = pd.concat([segmented, newRow.to_frame().T], ignore_index=True)
        startIndex += stride
        lastIndex += stride
    label = df['label'].loc[0]
    segmented['Label'] = [label for sample in segmented['Range']]
    return segmented
    

int1 = df.loc[df["label"] == "I1"]
int13 = df.loc[df["label"] == "I13"]

print(int1.shape[0])
print(int13.shape)
# print(df.shape)
print(int1.keys())
# print(df.iloc[0:256].to_numpy)

print(segmentation(int1).head())
# value = segmentation(int1).loc[0][1]

1108
(660, 2)
Index(['label', 'Standardised'], dtype='object')
     Range                                             Sample Label
0    0-256  [[[[-1.1555606530164928 -1.0370904823417137 -1...    I1
1  128-384  [[[[-0.7881556491245104 -0.38491921496522924 -...    I1
2  256-512  [[[[-1.0722477059962134 -0.9521059014768991 -1...    I1
3  384-640  [[[[-0.3467121707683465 -0.33774440045954907 -...    I1
4  512-768  [[[[-0.20748885033841907 0.01253283461941942 -...    I1
